In [184]:
import pandas as pd
import matplotlib as plt
import seaborn as sns
import json
import os
import re
from subprocess import call

In [5]:
# Load data
sl = '/'
home_path = f'/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache'
results_chris_path = f'{home_path}{sl}Part 3{sl}ChrisRuns{sl}Results'
results_jan_path = f'{home_path}{sl}Part 3'

In [6]:
def addNamePaths(chris, jan):
    return f'{results_chris_path}{sl}{chris}', f'{results_jan_path}{sl}{jan}'

similar = [
    addNamePaths('', '')
]

#resFile = open(f'{dir_output}\\TEMP\\stats.txt', 'r')
#regex_row = re.compile('([^ \t\n]+)[ \n\t]+([^ \t\n]+)[ \n\t]+([^ \t\n]+)')
#d = {'' if r is None else r.group(1): '' if r is None else r.group(2) for r in [regex_row.match(l) for l in resFile.read().splitlines()]}
#print(f'Instr cache miss: {d["system.cpu.icache.overall_miss_rate::total"]}, Data cache miss: {d["system.cpu.dcache.overall_miss_rate::total"]}, L2 Miss rate: {d["system.l2.overall_miss_rate::total"]}')

In [72]:
#ignore_keys = ['.system.cpu[0].workload[0].executable', '.system.cpu[0].workload[0].cwd', '.system.cpu[0].workload[0].cmd']
#ignore_keys = ['.system.cpu[0].workload[0].executable', '.system.cpu[0].workload[0].cwd', '.system.cpu[0].workload[0].cmd']

# Assumes c and d are the same structure with differing entries
def dictComp(d, c, r, **kwargs):
    do_print = kwargs['print'] if 'print' in kwargs else False
    ret = True
    for k in d.keys():
        if k in c:
            #Exceptions
            conc = f'{r}.{k}'
            if conc in ignore_keys:
                continue
            
            if conc == '.system.cpu':
                ret &= dictComp(d[k][0], c[k][0], conc+'[0]', **kwargs)
            elif conc == '.system.cpu[0].workload':
                ret &= dictComp(d[k][0], c[k][0], conc+'[0]', **kwargs)
            else:
                if conc == '.system.cpu[0].max_insts_any_thread' and c[k] != 500_000_000:
                    print(f'INSTRUCTION COUNT IS {c[k]} != 500M')
                
                if isinstance(c[k], dict):
                    ret &= dictComp(d[k], c[k], conc, **kwargs)
                elif d[k] != c[k]:
                    ret = False
                    if do_print:
                        print(f'{conc} differs: {d[k]} vs {c[k]}')
                    if conc == '.system.cpu[0].branchPred':
                            print('Different branch predictors used')
    return ret


def dictPull(d, v, r):
    ret = {}
    for k in d.keys():
        #Exceptions
        conc = f'{r}.{k}'

        if conc == '.system.cpu':
            ret.update(dictPull(d[k][0], v, conc+'[0]'))
        elif conc == '.system.cpu[0].workload':
            ret.update(dictPull(d[k][0], v, conc+'[0]'))
        else:
            if isinstance(d[k], dict):
                ret.update(dictPull(d[k], v, conc))
            elif conc in v:
                ret[conc] = d[k]
    return ret

#dictComp(a, b, '', print=False)
    

In [217]:
chris_files = f"""Perm_0_1_7_1_10_0_3_401.bzip2
Perm_6_2_6_2_2_12_3_401.bzip2
Perm_7_1_7_1_10_0_2_401.bzip2
Perm_7_1_7_1_1_0_3_401.bzip2
Perm_0_1_7_1_10_0_3_429.mcf
Perm_6_2_6_2_2_12_3_429.mcf
Perm_7_1_7_1_10_0_2_429.mcf
Perm_7_1_7_1_1_0_3_429.mcf
Perm_0_1_7_1_2_0_3_401.bzip2
Perm_6_2_6_3_1_12_3_401.bzip2
Perm_7_1_7_1_10_0_3_401.bzip2
Perm_7_1_7_1_2_0_0_401.bzip2
Perm_0_1_7_1_2_0_3_429.mcf
Perm_6_2_6_3_1_12_3_429.mcf
Perm_7_1_7_1_10_0_3_429.mcf
Perm_7_1_7_1_2_0_0_429.mcf
Perm_0_2_6_2_1_12_3_401.bzip2
Perm_6_2_7_2_1_12_3_401.bzip2
Perm_7_1_7_1_10_0_4_401.bzip2
Perm_7_1_7_1_2_0_3_401.bzip2
Perm_0_2_6_2_1_12_3_429.mcf
Perm_6_2_7_2_1_12_3_429.mcf
Perm_7_1_7_1_10_0_4_429.mcf
Perm_7_1_7_1_2_0_3_429.mcf
Perm_1_1_7_1_10_0_3_401.bzip2
Perm_6_3_6_2_1_12_3_401.bzip2
Perm_7_1_7_1_10_0_5_401.bzip2
Perm_7_1_7_1_2_0_6_401.bzip2
Perm_1_1_7_1_10_0_3_429.mcf
Perm_6_3_6_2_1_12_3_429.mcf
Perm_7_1_7_1_10_0_5_429.mcf
Perm_7_1_7_1_2_0_6_429.mcf
Perm_1_1_7_1_2_0_3_401.bzip2
Perm_7_0_7_1_10_0_3_401.bzip2
Perm_7_1_7_1_10_0_6_401.bzip2
Perm_7_1_7_1_2_14_3_401.bzip2
Perm_1_1_7_1_2_0_3_429.mcf
Perm_7_0_7_1_10_0_3_429.mcf
Perm_7_1_7_1_10_0_6_429.mcf
Perm_7_1_7_1_2_14_3_429.mcf
Perm_2_1_7_1_10_0_3_401.bzip2
Perm_7_0_7_1_2_0_3_401.bzip2
Perm_7_1_7_1_10_10_3_401.bzip2
Perm_7_1_7_1_3_0_3_401.bzip2
Perm_2_1_7_1_10_0_3_429.mcf
Perm_7_0_7_1_2_0_3_429.mcf
Perm_7_1_7_1_10_10_3_429.mcf
Perm_7_1_7_1_3_0_3_429.mcf
Perm_2_1_7_1_2_0_3_401.bzip2
Perm_7_1_0_1_10_0_3_401.bzip2
Perm_7_1_7_1_10_11_3_401.bzip2
Perm_7_1_7_1_4_0_3_401.bzip2
Perm_2_1_7_1_2_0_3_429.mcf
Perm_7_1_0_1_10_0_3_429.mcf
Perm_7_1_7_1_10_11_3_429.mcf
Perm_7_1_7_1_4_0_3_429.mcf
Perm_3_1_7_1_10_0_3_401.bzip2
Perm_7_1_0_1_2_0_3_401.bzip2
Perm_7_1_7_1_10_12_3_401.bzip2
Perm_7_1_7_1_5_0_3_401.bzip2
Perm_3_1_7_1_10_0_3_429.mcf
Perm_7_1_0_1_2_0_3_429.mcf
Perm_7_1_7_1_10_12_3_429.mcf
Perm_7_1_7_1_5_0_3_429.mcf
Perm_4_1_7_1_10_0_3_401.bzip2
Perm_7_1_1_1_10_0_3_401.bzip2
Perm_7_1_7_1_10_13_3_401.bzip2
Perm_7_1_7_1_6_0_3_401.bzip2
Perm_4_1_7_1_10_0_3_429.mcf
Perm_7_1_1_1_10_0_3_429.mcf
Perm_7_1_7_1_10_13_3_429.mcf
Perm_7_1_7_1_6_0_3_429.mcf
Perm_5_1_7_1_10_0_3_401.bzip2
Perm_7_1_2_1_10_0_3_401.bzip2
Perm_7_1_7_1_10_14_3_401.bzip2
Perm_7_1_7_1_7_0_3_401.bzip2
Perm_5_1_7_1_10_0_3_429.mcf
Perm_7_1_2_1_10_0_3_429.mcf
Perm_7_1_7_1_10_14_3_429.mcf
Perm_7_1_7_1_7_0_3_429.mcf
Perm_6_0_6_2_1_12_3_401.bzip2
Perm_7_1_3_1_10_0_3_401.bzip2
Perm_7_1_7_1_10_1_3_401.bzip2
Perm_7_1_7_1_8_0_3_401.bzip2
Perm_6_0_6_2_1_12_3_429.mcf
Perm_7_1_3_1_10_0_3_429.mcf
Perm_7_1_7_1_10_1_3_429.mcf
Perm_7_1_7_1_8_0_3_429.mcf
Perm_6_1_7_1_10_0_3_401.bzip2
Perm_7_1_4_1_10_0_3_401.bzip2
Perm_7_1_7_1_10_2_3_401.bzip2
Perm_7_1_7_1_9_0_3_401.bzip2
Perm_6_1_7_1_10_0_3_429.mcf
Perm_7_1_4_1_10_0_3_429.mcf
Perm_7_1_7_1_10_2_3_429.mcf
Perm_7_1_7_1_9_0_3_429.mcf
Perm_6_2_0_2_1_12_3_401.bzip2
Perm_7_1_5_1_10_0_3_401.bzip2
Perm_7_1_7_1_10_3_3_401.bzip2
Perm_7_1_7_2_10_0_3_401.bzip2
Perm_6_2_0_2_1_12_3_429.mcf
Perm_7_1_5_1_10_0_3_429.mcf
Perm_7_1_7_1_10_3_3_429.mcf
Perm_7_1_7_2_10_0_3_429.mcf
Perm_6_2_6_0_1_12_3_401.bzip2
Perm_7_1_6_1_10_0_3_401.bzip2
Perm_7_1_7_1_10_4_3_401.bzip2
Perm_7_1_7_3_10_0_3_401.bzip2
Perm_6_2_6_0_1_12_3_429.mcf
Perm_7_1_6_1_10_0_3_429.mcf
Perm_7_1_7_1_10_4_3_429.mcf
Perm_7_1_7_3_10_0_3_429.mcf
Perm_6_2_6_2_0_12_3_401.bzip2
Perm_7_1_7_0_10_0_3_401.bzip2
Perm_7_1_7_1_10_5_3_401.bzip2
Perm_7_1_7_3_2_0_3_401.bzip2
Perm_6_2_6_2_0_12_3_429.mcf
Perm_7_1_7_0_10_0_3_429.mcf
Perm_7_1_7_1_10_5_3_429.mcf
Perm_7_1_7_3_2_0_3_429.mcf
Perm_6_2_6_2_1_0_3_401.bzip2
Perm_7_1_7_0_2_0_3_401.bzip2
Perm_7_1_7_1_10_6_3_401.bzip2
Perm_7_2_6_2_1_12_3_401.bzip2
Perm_6_2_6_2_1_0_3_429.mcf
Perm_7_1_7_0_2_0_3_429.mcf
Perm_7_1_7_1_10_6_3_429.mcf
Perm_7_2_6_2_1_12_3_429.mcf
Perm_6_2_6_2_1_12_0_401.bzip2
Perm_7_1_7_1_0_0_3_401.bzip2
Perm_7_1_7_1_10_7_3_401.bzip2
Perm_7_2_7_1_10_0_3_401.bzip2
Perm_6_2_6_2_1_12_0_429.mcf
Perm_7_1_7_1_0_0_3_429.mcf
Perm_7_1_7_1_10_7_3_429.mcf
Perm_7_2_7_1_10_0_3_429.mcf
Perm_6_2_6_2_1_12_4_401.bzip2
Perm_7_1_7_1_10_0_0_401.bzip2
Perm_7_1_7_1_10_8_3_401.bzip2
Perm_7_3_7_1_10_0_3_401.bzip2
Perm_6_2_6_2_1_12_4_429.mcf
Perm_7_1_7_1_10_0_0_429.mcf
Perm_7_1_7_1_10_8_3_429.mcf
Perm_7_3_7_1_10_0_3_429.mcf
Perm_6_2_6_2_1_13_3_401.bzip2
Perm_7_1_7_1_10_0_1_401.bzip2
Perm_7_1_7_1_10_9_3_401.bzip2
Perm_7_3_7_1_2_0_3_401.bzip2
Perm_6_2_6_2_1_13_3_429.mcf
Perm_7_1_7_1_10_0_1_429.mcf
Perm_7_1_7_1_10_9_3_429.mcf
Perm_7_3_7_1_2_0_3_429.mcf""".split('\n')

jan_files = f"""JansRunsGood{sl}Baseline-Configuration401
JansRunsGood{sl}Baseline-Configuration429
JansRunsGood{sl}Cacheline size/Cacheline-128B-Configuration401
JansRunsGood{sl}Cacheline size/Cacheline-128B-Configuration429
JansRunsGood{sl}Cacheline size/Cacheline-16B-Configuration401
JansRunsGood{sl}Cacheline size/Cacheline-16B-Configuration429
JansRunsGood{sl}Cacheline size/Cacheline-256B-Configuration401
JansRunsGood{sl}Cacheline size/Cacheline-256B-Configuration429
JansRunsGood{sl}Cacheline size/Cacheline-32B-Configuration401
JansRunsGood{sl}Cacheline size/Cacheline-32B-Configuration429
JansRunsGood{sl}Cacheline size/Cacheline-512B-Configuration401
JansRunsGood{sl}Cacheline size/Cacheline-512B-Configuration429
JansRunsGood{sl}Cacheline size/Cacheline-8B-Configuration401
JansRunsGood{sl}Cacheline size/Cacheline-8B-Configuration429
JansRunsGood{sl}L1D Assoc/L1DAssoc-1-Configuration401
JansRunsGood{sl}L1D Assoc/L1DAssoc-1-Configuration429
JansRunsGood{sl}L1D Assoc/L1DAssoc-4-Configuration401
JansRunsGood{sl}L1D Assoc/L1DAssoc-4-Configuration429
JansRunsGood{sl}L1D Assoc/L1DAssoc-8-Configuration401
JansRunsGood{sl}L1D Assoc/L1DAssoc-8-Configuration429
JansRunsGood{sl}L1D Size/L1D-16KB-Configuration401
JansRunsGood{sl}L1D Size/L1D-16KB-Configuration429
JansRunsGood{sl}L1D Size/L1D-1KB-Configuration401
JansRunsGood{sl}L1D Size/L1D-1KB-Configuration429
JansRunsGood{sl}L1D Size/L1D-2KB-Configuration401
JansRunsGood{sl}L1D Size/L1D-2KB-Configuration429
JansRunsGood{sl}L1D Size/L1D-32KB-Configuration401
JansRunsGood{sl}L1D Size/L1D-32KB-Configuration429
JansRunsGood{sl}L1D Size/L1D-4KB-Configuration401
JansRunsGood{sl}L1D Size/L1D-4KB-Configuration429
JansRunsGood{sl}L1D Size/L1D-64KB-Configuration401
JansRunsGood{sl}L1D Size/L1D-64KB-Configuration429
JansRunsGood{sl}L1D Size/L1D-8KB-Configuration401
JansRunsGood{sl}L1D Size/L1D-8KB-Configuration429
JansRunsGood{sl}L1I Assoc/L1IAssoc-1-Configuration401
JansRunsGood{sl}L1I Assoc/L1IAssoc-1-Configuration429
JansRunsGood{sl}L1I Assoc/L1IAssoc-4-Configuration401
JansRunsGood{sl}L1I Assoc/L1IAssoc-4-Configuration429
JansRunsGood{sl}L1I Assoc/L1IAssoc-8-Configuration401
JansRunsGood{sl}L1I Assoc/L1IAssoc-8-Configuration429
JansRunsGood{sl}L1I Size/L1I-16KB-Configuration401
JansRunsGood{sl}L1I Size/L1I-16KB-Configuration429
JansRunsGood{sl}L1I Size/L1I-1KB-Configuration401
JansRunsGood{sl}L1I Size/L1I-1KB-Configuration429
JansRunsGood{sl}L1I Size/L1I-2KB-Configuration401
JansRunsGood{sl}L1I Size/L1I-2KB-Configuration429
JansRunsGood{sl}L1I Size/L1I-32KB-Configuration401
JansRunsGood{sl}L1I Size/L1I-32KB-Configuration429
JansRunsGood{sl}L1I Size/L1I-4KB-Configuration401
JansRunsGood{sl}L1I Size/L1I-4KB-Configuration429
JansRunsGood{sl}L1I Size/L1I-64KB-Configuration401
JansRunsGood{sl}L1I Size/L1I-64KB-Configuration429
JansRunsGood{sl}L1I Size/L1I-8KB-Configuration401
JansRunsGood{sl}L1I Size/L1I-8KB-Configuration429
JansRunsGood{sl}L2 Assoc/L2Assoc-1024-Configuration401
JansRunsGood{sl}L2 Assoc/L2Assoc-1024-Configuration429
JansRunsGood{sl}L2 Assoc/L2Assoc-128-Configuration401
JansRunsGood{sl}L2 Assoc/L2Assoc-128-Configuration429
JansRunsGood{sl}L2 Assoc/L2Assoc-16-Configuration401
JansRunsGood{sl}L2 Assoc/L2Assoc-16-Configuration429
JansRunsGood{sl}L2 Assoc/L2Assoc-16384-Configuration401
JansRunsGood{sl}L2 Assoc/L2Assoc-16384-Configuration429
JansRunsGood{sl}L2 Assoc/L2Assoc-2-Configuration401
JansRunsGood{sl}L2 Assoc/L2Assoc-2-Configuration429
JansRunsGood{sl}L2 Assoc/L2Assoc-2048-Configuration401
JansRunsGood{sl}L2 Assoc/L2Assoc-2048-Configuration429
JansRunsGood{sl}L2 Assoc/L2Assoc-256-Configuration401
JansRunsGood{sl}L2 Assoc/L2Assoc-256-Configuration429
JansRunsGood{sl}L2 Assoc/L2Assoc-32-Configuration401
JansRunsGood{sl}L2 Assoc/L2Assoc-32-Configuration429
JansRunsGood{sl}L2 Assoc/L2Assoc-4-Configuration401
JansRunsGood{sl}L2 Assoc/L2Assoc-4-Configuration429
JansRunsGood{sl}L2 Assoc/L2Assoc-4096-Configuration401
JansRunsGood{sl}L2 Assoc/L2Assoc-4096-Configuration429
JansRunsGood{sl}L2 Assoc/L2Assoc-512-Configuration401
JansRunsGood{sl}L2 Assoc/L2Assoc-512-Configuration429
JansRunsGood{sl}L2 Assoc/L2Assoc-64-Configuration401
JansRunsGood{sl}L2 Assoc/L2Assoc-64-Configuration429
JansRunsGood{sl}L2 Assoc/L2Assoc-8-Configuration401
JansRunsGood{sl}L2 Assoc/L2Assoc-8-Configuration429
JansRunsGood{sl}L2 Assoc/L2Assoc-8192-Configuration401
JansRunsGood{sl}L2 Assoc/L2Assoc-8192-Configuration429
JansRunsGood{sl}L2 Size/L2-128KB-Configuration401
JansRunsGood{sl}L2 Size/L2-128KB-Configuration429
JansRunsGood{sl}L2 Size/L2-16KB-Configuration401
JansRunsGood{sl}L2 Size/L2-16KB-Configuration429
JansRunsGood{sl}L2 Size/L2-1KB-Configuration401
JansRunsGood{sl}L2 Size/L2-1KB-Configuration429
JansRunsGood{sl}L2 Size/L2-256KB-Configuration401
JansRunsGood{sl}L2 Size/L2-256KB-Configuration429
JansRunsGood{sl}L2 Size/L2-2KB-Configuration401
JansRunsGood{sl}L2 Size/L2-2KB-Configuration429
JansRunsGood{sl}L2 Size/L2-32KB-Configuration401
JansRunsGood{sl}L2 Size/L2-32KB-Configuration429
JansRunsGood{sl}L2 Size/L2-4KB-Configuration401
JansRunsGood{sl}L2 Size/L2-4KB-Configuration429
JansRunsGood{sl}L2 Size/L2-512KB-Configuration401
JansRunsGood{sl}L2 Size/L2-512KB-Configuration429
JansRunsGood{sl}L2 Size/L2-64KB-Configuration401
JansRunsGood{sl}L2 Size/L2-64KB-Configuration429
JansRunsGood{sl}L2 Size/L2-8KB-Configuration401
JansRunsGood{sl}L2 Size/L2-8KB-Configuration429""".split('\n')

#Removed JanRuns since they all have 500k instrs instead of 500m
"""JanRuns{sl}Cacheline{sl}HiCachelineConfiguration401
JanRuns{sl}Cacheline{sl}LowCachelineConfiguration401
JanRuns{sl}Cacheline{sl}HiCachelineConfiguration429
JanRuns{sl}Cacheline{sl}LowCachelineConfiguration429
JanRuns{sl}L1D Assoc{sl}HiL1DAssocConfiguration401
JanRuns{sl}L1D Assoc{sl}LowL1DAssocConfiguration401
JanRuns{sl}L1D Assoc{sl}HiL1DAssocConfiguration429
JanRuns{sl}L1D Assoc{sl}LowL1DAssocConfiguration429
JanRuns{sl}L1D Size{sl}HiL1DConfiguration401
JanRuns{sl}L1D Size{sl}LowL1DConfiguration401
JanRuns{sl}L1D Size{sl}MedL1DConfiguration401
JanRuns{sl}L1D Size{sl}HiL1DConfiguration429
JanRuns{sl}L1D Size{sl}LowL1DConfiguration429
JanRuns{sl}L1D Size{sl}MedL1DConfiguration429
JanRuns{sl}L1I Assoc{sl}HiL1IAssocConfiguration401
JanRuns{sl}L1I Assoc{sl}LowL1IAssocConfiguration401
JanRuns{sl}L1I Assoc{sl}HiL1IAssocConfiguration429
JanRuns{sl}L1I Assoc{sl}LowL1IAssocConfiguration429
JanRuns{sl}L1I Size{sl}HiL1IConfiguration401
JanRuns{sl}L1I Size{sl}LowL1IConfiguration401
JanRuns{sl}L1I Size{sl}HiL1IConfiguration429
JanRuns{sl}L1I Size{sl}LowL1IConfiguration429
JanRuns{sl}L2 Size{sl}HiL2Configuration401
JanRuns{sl}L2 Size{sl}LowL2Configuration401
JanRuns{sl}L2 Size{sl}HiL2Configuration429
JanRuns{sl}L2 Size{sl}LowL2Configuration429
JanRuns{sl}L2 Assoc{sl}HiL2AssocConfiguration401
JanRuns{sl}L2 Assoc{sl}LowL2AssocConfiguration401
JanRuns{sl}L2 Assoc{sl}HiL2AssocConfiguration429
JanRuns{sl}L2 Assoc{sl}LowL2AssocConfiguration429"""

n = 'config.json'

chris_files = [f'{results_chris_path}{sl}{v}{sl}{n}' for v in chris_files]
jan_files = [f'{results_jan_path}{sl}{v}{sl}{n}' for v in jan_files]

rescombs_t = []
for i in chris_files:
    a = json.loads(open(i).read())
    #print(i)
    for j in jan_files:
        b = json.loads(open(j).read())
        print(f'Paths:\n{i}\n{j}')
        c = dictComp(a, b, '', print=False)
        print('\n')
        if c:
            l = len(home_path)
            rescombs_t.append((i[l:], j[l:]))
    print('--------')

rescombs = []
for x, y in rescombs_t:
    a = x[:-len('config.json')-1]
    b = y[:-len('config.json')-1]
    print(f'{a}\n{b}')
    i = a.index('.')
    a = a[i-3:i]
    b = b[-3:]
    print(f'{a}\n{b}\n')
    if(a == b):
        rescombs.append((x, y))
        
rescombs

Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_0_1_7_1_10_0_3_401.bzip2/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/Baseline-Configuration401/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_0_1_7_1_10_0_3_401.bzip2/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/Baseline-Configuration429/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_0_1_7_1_10_0_3_401.bzip2/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/Cacheline size/Cacheline-128B-Configuration401/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_0_1_7_1_10_0_3_401.bzip2/config.json
/Users

Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_1_0_3_401.bzip2/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/Cacheline size/Cacheline-32B-Configuration401/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_1_0_3_401.bzip2/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/Cacheline size/Cacheline-32B-Configuration429/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_1_0_3_401.bzip2/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/Cacheline size/Cacheline-512B-Configuration401/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_

Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_10_0_2_429.mcf/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/L2 Size/L2-64KB-Configuration401/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_10_0_2_429.mcf/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/L2 Size/L2-64KB-Configuration429/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_10_0_2_429.mcf/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/L2 Size/L2-8KB-Configuration401/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_10_0_2_429.mcf/config.json
/Users/chrszlr/

Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_2_0_0_401.bzip2/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/Cacheline size/Cacheline-32B-Configuration401/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_2_0_0_401.bzip2/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/Cacheline size/Cacheline-32B-Configuration429/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_2_0_0_401.bzip2/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/Cacheline size/Cacheline-512B-Configuration401/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_

Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_2_0_0_429.mcf/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/Cacheline size/Cacheline-256B-Configuration429/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_2_0_0_429.mcf/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/Cacheline size/Cacheline-32B-Configuration401/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_2_0_0_429.mcf/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/Cacheline size/Cacheline-32B-Configuration429/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_2_0_

...

Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_10_8_3_401.bzip2/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/L2 Size/L2-128KB-Configuration401/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_10_8_3_401.bzip2/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/L2 Size/L2-128KB-Configuration429/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_10_8_3_401.bzip2/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/L2 Size/L2-16KB-Configuration401/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_10_8_3_401.bzip2/config.json
/Use

Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_10_8_3_429.mcf/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/L2 Size/L2-32KB-Configuration401/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_10_8_3_429.mcf/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/L2 Size/L2-32KB-Configuration429/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_10_8_3_429.mcf/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/L2 Size/L2-4KB-Configuration401/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_10_8_3_429.mcf/config.json
/Users/chrszlr/

Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_10_9_3_401.bzip2/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/L2 Size/L2-16KB-Configuration401/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_10_9_3_401.bzip2/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/L2 Size/L2-16KB-Configuration429/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_10_9_3_401.bzip2/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/L2 Size/L2-1KB-Configuration401/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_10_9_3_401.bzip2/config.json
/Users/

Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_10_9_3_429.mcf/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/L2 Size/L2-32KB-Configuration401/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_10_9_3_429.mcf/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/L2 Size/L2-32KB-Configuration429/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_10_9_3_429.mcf/config.json
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/JansRunsGood/L2 Size/L2-4KB-Configuration401/config.json


Paths:
/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_10_9_3_429.mcf/config.json
/Users/chrszlr/

[('/Part 3/ChrisRuns/Results/Perm_0_1_7_1_10_0_3_401.bzip2/config.json',
  '/Part 3/JansRunsGood/L1D Size/L1D-1KB-Configuration401/config.json'),
 ('/Part 3/ChrisRuns/Results/Perm_7_1_7_1_10_0_2_401.bzip2/config.json',
  '/Part 3/JansRunsGood/Cacheline size/Cacheline-32B-Configuration401/config.json'),
 ('/Part 3/ChrisRuns/Results/Perm_7_1_7_1_1_0_3_401.bzip2/config.json',
  '/Part 3/JansRunsGood/L2 Size/L2-2KB-Configuration401/config.json'),
 ('/Part 3/ChrisRuns/Results/Perm_0_1_7_1_10_0_3_429.mcf/config.json',
  '/Part 3/JansRunsGood/L1D Size/L1D-1KB-Configuration429/config.json'),
 ('/Part 3/ChrisRuns/Results/Perm_7_1_7_1_10_0_2_429.mcf/config.json',
  '/Part 3/JansRunsGood/Cacheline size/Cacheline-32B-Configuration429/config.json'),
 ('/Part 3/ChrisRuns/Results/Perm_7_1_7_1_1_0_3_429.mcf/config.json',
  '/Part 3/JansRunsGood/L2 Size/L2-2KB-Configuration429/config.json'),
 ('/Part 3/ChrisRuns/Results/Perm_0_1_7_1_2_0_3_401.bzip2/config.json',
  '/Part 3/JansRunsGood/L1D Size/L1D-1KB

In [221]:
regex_row = re.compile('([^ \t\n]+)[ \n\t]+([^ \t\n]+)[ \n\t]+([^ \t\n]+)')

def getDictFromStats(path):
    d = open(path, 'r').read().splitlines()
    return {'' if r is None else r.group(1): '' if r is None else r.group(2) for r in [regex_row.match(l) for l in d]}

for path_a, path_b in rescombs:
    path_a_sub = path_a[:-len('config.json')]
    path_b_sub = path_b[:-len('config.json')]
    d1 = getDictFromStats(home_path+path_a_sub+'stats.txt')
    d2 = getDictFromStats(home_path+path_b_sub+'stats.txt')
    #print(d1)
    k = ['system.cpu.icache.overall_miss_rate::total', 'system.cpu.dcache.overall_miss_rate::total', 'system.l2.overall_miss_rate::total']
    kr = True
    for v in k:
        kr &= abs(float(d1[v]) - float(d2[v])) < .01
    if not kr:
        print(path_a_sub)
        print(f'Instr cache miss: {d1["system.cpu.icache.overall_miss_rate::total"]}, Data cache miss: {d1["system.cpu.dcache.overall_miss_rate::total"]}, L2 Miss rate: {d1["system.l2.overall_miss_rate::total"]}')
        print(path_b_sub)
        print(f'Instr cache miss: {d2["system.cpu.icache.overall_miss_rate::total"]}, Data cache miss: {d2["system.cpu.dcache.overall_miss_rate::total"]}, L2 Miss rate: {d2["system.l2.overall_miss_rate::total"]}')
        print('\n')

#resFile = open(f'{dir_output}/TEMP/stats.txt', 'r')
#regex_row = re.compile('([^ \t\n]+)[ \n\t]+([^ \t\n]+)[ \n\t]+([^ \t\n]+)')
#d = {'' if r is None else r.group(1): '' if r is None else r.group(2) for r in [regex_row.match(l) for l in resFile.read().splitlines()]}
#print(f'Instr cache miss: {d["system.cpu.icache.overall_miss_rate::total"]}, Data cache miss: {d["system.cpu.dcache.overall_miss_rate::total"]}, L2 Miss rate: {d["system.l2.overall_miss_rate::total"]}')

/Part 3/ChrisRuns/Results/Perm_0_1_7_1_10_0_3_429.mcf/
Instr cache miss: 0.000001, Data cache miss: 0.155717, L2 Miss rate: 0.147445
/Part 3/JansRunsGood/L1D Size/L1D-1KB-Configuration429/
Instr cache miss: 0.000001, Data cache miss: 0.135920, L2 Miss rate: 0.169119


/Part 3/ChrisRuns/Results/Perm_0_1_7_1_2_0_3_429.mcf/
Instr cache miss: 0.000001, Data cache miss: 0.155717, L2 Miss rate: 0.147445
/Part 3/JansRunsGood/L1D Size/L1D-1KB-Configuration429/
Instr cache miss: 0.000001, Data cache miss: 0.135920, L2 Miss rate: 0.169119


/Part 3/ChrisRuns/Results/Perm_2_1_7_1_10_0_3_429.mcf/
Instr cache miss: 0.000001, Data cache miss: 0.069563, L2 Miss rate: 0.329414
/Part 3/JansRunsGood/L1D Size/L1D-4KB-Configuration429/
Instr cache miss: 0.000001, Data cache miss: 0.072917, L2 Miss rate: 0.314797


/Part 3/ChrisRuns/Results/Perm_2_1_7_1_2_0_3_429.mcf/
Instr cache miss: 0.000001, Data cache miss: 0.069563, L2 Miss rate: 0.329414
/Part 3/JansRunsGood/L1D Size/L1D-4KB-Configuration429/
Instr 

In [19]:
t = ['system', 'cpu']
ra, rb = (a, b)
for v in t:
    ra = ra[v]
    rb = rb[v]
print(f'A: {ra}, B: {rb}')

A: [{'do_statistics_insts': True, 'numThreads': 1, 'itb': {'name': 'itb', 'eventq_index': 0, 'cxx_class': 'X86ISA::TLB', 'walker': {'name': 'walker', 'clk_domain': 'system.cpu_clk_domain', 'system': 'system', 'eventq_index': 0, 'cxx_class': 'X86ISA::Walker', 'path': 'system.cpu.itb.walker', 'type': 'X86PagetableWalker', 'port': {'peer': 'system.cpu.itb_walker_cache.cpu_side', 'role': 'MASTER'}, 'num_squash_per_cycle': 4}, 'path': 'system.cpu.itb', 'type': 'X86TLB', 'size': 64}, 'system': 'system', 'dtb_walker_cache': {'cpu_side': {'peer': 'system.cpu.dtb.walker.port', 'role': 'SLAVE'}, 'clusivity': 'mostly_incl', 'prefetcher': None, 'clk_domain': 'system.cpu_clk_domain', 'write_buffers': 8, 'response_latency': 2, 'cxx_class': 'Cache', 'size': 1024, 'tags': {'name': 'tags', 'eventq_index': 0, 'hit_latency': 2, 'clk_domain': 'system.cpu_clk_domain', 'sequential_access': False, 'assoc': 2, 'cxx_class': 'LRU', 'path': 'system.cpu.dtb_walker_cache.tags', 'block_size': 8, 'type': 'LRU', 'siz

In [141]:
configs_legacy = {
        '.system.cpu[0].dcache.size': [
                1024, 2048, 4096, 8192, 16384, 32768, 65536, 131072
        ],
        '.system.cpu[0].dcache.assoc': [
                1, 2, 4, 8
        ],
        '.system.cpu[0].icache.size': [
                1024, 2048, 4096, 8192, 16384, 32768, 65536, 131072
        ],
        '.system.cpu[0].icache.assoc': [
                1, 2, 4, 8
        ],
        '.system.l2.size': [
                262144, 524288, 1048576
        ],
        '.system.l2.assoc': [
                1, 2, 4, 8, 16, 32, 64, 128, 256, 512, 1024, 2048, 4096, 8192, 16384
        ],
        '.system.cache_line_size': [
                8, 16, 32, 64, 128, 256, 512
        ]
}

configs = {
        '.system.cpu[0].dcache.size': [
                1024, 2048, 4096, 8192, 16384, 32768, 65536, 131072
        ],
        '.system.cpu[0].dcache.assoc': [
                1, 2, 4, 8
        ],
        '.system.cpu[0].icache.size': [
                1024, 2048, 4096, 8192, 16384, 32768, 65536, 131072
        ],
        '.system.cpu[0].icache.assoc': [
                1, 2, 4, 8
        ],
        '.system.l2.size': [
                1024, 2048, 4096, 8192, 16384, 32768, 65536, 131072, 262144, 524288, 1048576
        ],
        '.system.l2.assoc': [
                1, 2, 4, 8, 16, 32, 64, 128, 256, 512, 1024, 2048, 4096, 8192, 16384
        ],
        '.system.cache_line_size': [
                8, 16, 32, 64, 128, 256, 512
        ]
}

In [193]:
take = ['.system.cache_line_size', '.system.cpu[0].max_insts_any_thread',
        '.system.cpu[0].icache.size', '.system.cpu[0].icache.assoc',
        '.system.cpu[0].dcache.size', '.system.cpu[0].dcache.assoc',
        '.system.l2.size', '.system.l2.assoc']

#to_check = jan_files
to_check = chris_files
all_vals = []
for path_sub in to_check:
    path = f'{path_sub}'
    a = json.loads(open(path).read())
    print(path_sub[len(home_path)+1:])
    p = dictPull(a, take, '')
    all_vals.append(p)
    print(p)
    #d = getDictFromStats(path+'stats.txt')
    #print(d1)
    #print(path)
    #print(f'Instr cache miss: {d["system.cpu.icache.overall_miss_rate::total"]}, Data cache miss: {d["system.cpu.dcache.overall_miss_rate::total"]}, L2 Miss rate: {d["system.l2.overall_miss_rate::total"]}')
    #print('\n')

Part 3/ChrisRuns/Results/Perm_0_1_7_1_2_0_3_401.bzip2/config.json
{'.system.cache_line_size': 64, '.system.cpu[0].icache.size': 131072, '.system.cpu[0].icache.assoc': 2, '.system.cpu[0].max_insts_any_thread': 500000000, '.system.cpu[0].dcache.size': 1024, '.system.cpu[0].dcache.assoc': 2, '.system.l2.size': 1048576, '.system.l2.assoc': 1}
Part 3/ChrisRuns/Results/Perm_6_2_6_2_0_12_3_401.bzip2/config.json
{'.system.cache_line_size': 64, '.system.cpu[0].icache.size': 65536, '.system.cpu[0].icache.assoc': 4, '.system.cpu[0].max_insts_any_thread': 500000000, '.system.cpu[0].dcache.size': 65536, '.system.cpu[0].dcache.assoc': 4, '.system.l2.size': 262144, '.system.l2.assoc': 4096}
Part 3/ChrisRuns/Results/Perm_6_2_7_2_1_12_3_401.bzip2/config.json
{'.system.cache_line_size': 64, '.system.cpu[0].icache.size': 131072, '.system.cpu[0].icache.assoc': 4, '.system.cpu[0].max_insts_any_thread': 500000000, '.system.cpu[0].dcache.size': 65536, '.system.cpu[0].dcache.assoc': 4, '.system.l2.size': 5242

In [194]:
new_runs_t = []
for c in all_vals:
    print(c)
    run = [configs[k].index(c[k]) for k in configs.keys()]
    new_runs_t.append(run)

for i in range(0,len(all_vals)):
    print(f'{to_check[i]}\n{new_runs_t[i]}\n')
    
new_runs = []
[new_runs.append(v) for v in new_runs_t if v not in new_runs]
print(f'Unique\n{new_runs}')

{'.system.cache_line_size': 64, '.system.cpu[0].icache.size': 131072, '.system.cpu[0].icache.assoc': 2, '.system.cpu[0].max_insts_any_thread': 500000000, '.system.cpu[0].dcache.size': 1024, '.system.cpu[0].dcache.assoc': 2, '.system.l2.size': 1048576, '.system.l2.assoc': 1}
{'.system.cache_line_size': 64, '.system.cpu[0].icache.size': 65536, '.system.cpu[0].icache.assoc': 4, '.system.cpu[0].max_insts_any_thread': 500000000, '.system.cpu[0].dcache.size': 65536, '.system.cpu[0].dcache.assoc': 4, '.system.l2.size': 262144, '.system.l2.assoc': 4096}
{'.system.cache_line_size': 64, '.system.cpu[0].icache.size': 131072, '.system.cpu[0].icache.assoc': 4, '.system.cpu[0].max_insts_any_thread': 500000000, '.system.cpu[0].dcache.size': 65536, '.system.cpu[0].dcache.assoc': 4, '.system.l2.size': 524288, '.system.l2.assoc': 4096}
{'.system.cache_line_size': 64, '.system.cpu[0].icache.size': 131072, '.system.cpu[0].icache.assoc': 2, '.system.cpu[0].max_insts_any_thread': 500000000, '.system.cpu[0].

In [118]:
a = '/Part 3/ChrisRuns/Results/Perm_7_1_7_1_2_0_3_429.mcf/'
b = 'Part 3/JanRuns/Cacheline/HiCachelineConfiguration429/'
b[-4:-1]
a[a.index('.')+1:-1]

'bzip2'

In [149]:
f'_{"_".join([str(v) for v in [1, 2, 3, 4, 5, 6]])}_'

'_1_2_3_4_5_6_'

In [189]:
for i in range(0,len(all_vals)):
    a = to_check[i]
    print(f'{a}\n{new_runs_t[i]}')
    sub = a[:-len('config.json')-1]
    s = sub.index('_')
    ne = sub[::-1].index('_')
    #print(f'{a[:s]} | {a[-ne:]}')
    a = sub[:s] + f'_{"_".join([str(v) for v in new_runs_t[i]])}_' + sub[-ne:]
    #print(f'{a}')
    print(f'mv {sub} {a}\n')
    call(f'mv {sub} {a}', shell=True)

/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_0_1_7_1_2_0_3_401.bzip2/config.json
[0, 1, 7, 1, 10, 0, 3]
mv /Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_0_1_7_1_2_0_3_401.bzip2 /Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_0_1_7_1_10_0_3_401.bzip2

/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_6_2_6_2_0_12_3_401.bzip2/config.json
[6, 2, 6, 2, 8, 12, 3]
mv /Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_6_2_6_2_0_12_3_401.bzip2 /Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_6_2_6_2_8_12_3_401.bzip2

/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_6_2_7_2_1_12_3_401.bzip2/config.json
[6, 2, 7, 2, 9, 12, 3]
mv /Use

mv: 3/ChrisRuns/Results/Perm_0_1_7_1_10_0_3_401.bzip2 is not a directory
mv: 3/ChrisRuns/Results/Perm_6_2_6_2_8_12_3_401.bzip2 is not a directory
mv: 3/ChrisRuns/Results/Perm_6_2_7_2_9_12_3_401.bzip2 is not a directory
mv: 3/ChrisRuns/Results/Perm_7_1_7_1_10_0_3_401.bzip2 is not a directory
mv: 3/ChrisRuns/Results/Perm_0_1_7_1_10_0_3_429.mcf is not a directory
mv: 3/ChrisRuns/Results/Perm_6_2_6_2_8_12_3_429.mcf is not a directory
mv: 3/ChrisRuns/Results/Perm_6_2_7_2_9_12_3_429.mcf is not a directory
mv: 3/ChrisRuns/Results/Perm_7_1_7_1_10_0_3_429.mcf is not a directory
mv: 3/ChrisRuns/Results/Perm_0_2_6_2_9_12_3_401.bzip2 is not a directory
mv: 3/ChrisRuns/Results/Perm_6_2_6_2_9_0_3_401.bzip2 is not a directory
mv: 3/ChrisRuns/Results/Perm_6_3_6_2_9_12_3_401.bzip2 is not a directory
mv: 3/ChrisRuns/Results/Perm_7_1_7_1_10_0_6_401.bzip2 is not a directory
mv: 3/ChrisRuns/Results/Perm_0_2_6_2_9_12_3_429.mcf is not a directory
mv: 3/ChrisRuns/Results/Perm_6_2_6_2_9_0_3_429.mcf is not a di

/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_2_14_3_401.bzip2/config.json
[7, 1, 7, 1, 10, 14, 3]
mv /Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_2_14_3_401.bzip2 /Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_1_10_14_3_401.bzip2

/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_1_1_7_1_2_0_3_429.mcf/config.json
[1, 1, 7, 1, 10, 0, 3]
mv /Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_1_1_7_1_2_0_3_429.mcf /Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_1_1_7_1_10_0_3_429.mcf

/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_6_2_6_2_1_12_0_429.mcf/config.json
[6, 2, 6, 2, 9, 12, 0]
mv /Users/chr

mv: 3/ChrisRuns/Results/Perm_6_2_6_2_9_12_0_429.mcf is not a directory
mv: 3/ChrisRuns/Results/Perm_7_0_7_1_10_0_3_429.mcf is not a directory
mv: 3/ChrisRuns/Results/Perm_7_1_7_1_10_14_3_429.mcf is not a directory
mv: 3/ChrisRuns/Results/Perm_2_1_7_1_10_0_3_401.bzip2 is not a directory
mv: 3/ChrisRuns/Results/Perm_6_2_6_2_9_12_4_401.bzip2 is not a directory
mv: 3/ChrisRuns/Results/Perm_7_1_0_1_10_0_3_401.bzip2 is not a directory
mv: 3/ChrisRuns/Results/Perm_7_1_7_3_10_0_3_401.bzip2 is not a directory
mv: 3/ChrisRuns/Results/Perm_2_1_7_1_10_0_3_429.mcf is not a directory
mv: 3/ChrisRuns/Results/Perm_6_2_6_2_9_12_4_429.mcf is not a directory
mv: 3/ChrisRuns/Results/Perm_7_1_0_1_10_0_3_429.mcf is not a directory
mv: 3/ChrisRuns/Results/Perm_7_1_7_3_10_0_3_429.mcf is not a directory
mv: 3/ChrisRuns/Results/Perm_6_0_6_2_9_12_3_401.bzip2 is not a directory
mv: 3/ChrisRuns/Results/Perm_6_2_6_2_9_13_3_401.bzip2 is not a directory
mv: 3/ChrisRuns/Results/Perm_7_1_7_0_10_0_3_401.bzip2 is not a d

/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_0_2_0_3_401.bzip2/config.json
[7, 1, 7, 0, 10, 0, 3]
mv /Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_0_2_0_3_401.bzip2 /Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_1_7_0_10_0_3_401.bzip2

/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_2_6_2_1_12_3_401.bzip2/config.json
[7, 2, 6, 2, 9, 12, 3]
mv /Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_2_6_2_1_12_3_401.bzip2 /Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_7_2_6_2_9_12_3_401.bzip2

/Users/chrszlr/Documents/School/Classes/CS 6304/Proj2/ProjectTwo-Cache/Part 3/ChrisRuns/Results/Perm_6_0_6_2_1_12_3_429.mcf/config.json
[6, 0, 6, 2, 9, 12, 3]
mv /Users

mv: 3/ChrisRuns/Results/Perm_6_2_6_2_9_13_3_429.mcf is not a directory
mv: 3/ChrisRuns/Results/Perm_7_1_7_0_10_0_3_429.mcf is not a directory
mv: 3/ChrisRuns/Results/Perm_7_2_6_2_9_12_3_429.mcf is not a directory
mv: 3/ChrisRuns/Results/Perm_6_2_0_2_9_12_3_401.bzip2 is not a directory
mv: 3/ChrisRuns/Results/Perm_6_2_6_2_10_12_3_401.bzip2 is not a directory
mv: 3/ChrisRuns/Results/Perm_7_1_7_1_8_0_3_401.bzip2 is not a directory
mv: 3/ChrisRuns/Results/Perm_7_3_7_1_10_0_3_401.bzip2 is not a directory
mv: 3/ChrisRuns/Results/Perm_6_2_0_2_9_12_3_429.mcf is not a directory
mv: 3/ChrisRuns/Results/Perm_6_2_6_2_10_12_3_429.mcf is not a directory
mv: 3/ChrisRuns/Results/Perm_7_1_7_1_8_0_3_429.mcf is not a directory
mv: 3/ChrisRuns/Results/Perm_7_3_7_1_10_0_3_429.mcf is not a directory
mv: 3/ChrisRuns/Results/Perm_6_2_6_0_9_12_3_401.bzip2 is not a directory
mv: 3/ChrisRuns/Results/Perm_6_2_6_3_9_12_3_401.bzip2 is not a directory
mv: 3/ChrisRuns/Results/Perm_7_1_7_1_10_0_0_401.bzip2 is not a di

In [195]:
a = [[7, 1, 7, 1, 10, 0, 3], [7, 1, 7, 1, 10, 0, 4], [7, 1, 7, 1, 10, 0, 1], [7, 1, 7, 1, 10, 0, 5], [7, 1, 7, 1, 10, 0, 2], [7, 1, 7, 1, 10, 0, 6], [7, 1, 7, 1, 10, 0, 0], [7, 0, 7, 1, 10, 0, 3], [7, 2, 7, 1, 10, 0, 3], [7, 3, 7, 1, 10, 0, 3], [4, 1, 7, 1, 10, 0, 3], [0, 1, 7, 1, 10, 0, 3], [1, 1, 7, 1, 10, 0, 3], [5, 1, 7, 1, 10, 0, 3], [2, 1, 7, 1, 10, 0, 3], [6, 1, 7, 1, 10, 0, 3], [3, 1, 7, 1, 10, 0, 3], [7, 1, 7, 0, 10, 0, 3], [7, 1, 7, 2, 10, 0, 3], [7, 1, 7, 3, 10, 0, 3], [7, 1, 4, 1, 10, 0, 3], [7, 1, 0, 1, 10, 0, 3], [7, 1, 1, 1, 10, 0, 3], [7, 1, 5, 1, 10, 0, 3], [7, 1, 2, 1, 10, 0, 3], [7, 1, 6, 1, 10, 0, 3], [7, 1, 3, 1, 10, 0, 3], [7, 1, 7, 1, 10, 10, 3], [7, 1, 7, 1, 10, 7, 3], [7, 1, 7, 1, 10, 4, 3], [7, 1, 7, 1, 10, 14, 3], [7, 1, 7, 1, 10, 1, 3], [7, 1, 7, 1, 10, 11, 3], [7, 1, 7, 1, 10, 8, 3], [7, 1, 7, 1, 10, 5, 3], [7, 1, 7, 1, 10, 2, 3], [7, 1, 7, 1, 10, 12, 3], [7, 1, 7, 1, 10, 9, 3], [7, 1, 7, 1, 10, 6, 3], [7, 1, 7, 1, 10, 3, 3], [7, 1, 7, 1, 10, 13, 3], [7, 1, 7, 1, 7, 0, 3], [7, 1, 7, 1, 4, 0, 3], [7, 1, 7, 1, 0, 0, 3], [7, 1, 7, 1, 8, 0, 3], [7, 1, 7, 1, 1, 0, 3], [7, 1, 7, 1, 5, 0, 3], [7, 1, 7, 1, 2, 0, 3], [7, 1, 7, 1, 9, 0, 3], [7, 1, 7, 1, 6, 0, 3], [7, 1, 7, 1, 3, 0, 3]]
b = [[0, 1, 7, 1, 10, 0, 3], [6, 2, 6, 2, 8, 12, 3], [6, 2, 7, 2, 9, 12, 3], [7, 1, 7, 1, 10, 0, 3], [0, 2, 6, 2, 9, 12, 3], [6, 2, 6, 2, 9, 0, 3], [6, 3, 6, 2, 9, 12, 3], [7, 1, 7, 1, 10, 0, 6], [1, 1, 7, 1, 10, 0, 3], [6, 2, 6, 2, 9, 12, 0], [7, 0, 7, 1, 10, 0, 3], [7, 1, 7, 1, 10, 14, 3], [2, 1, 7, 1, 10, 0, 3], [6, 2, 6, 2, 9, 12, 4], [7, 1, 0, 1, 10, 0, 3], [7, 1, 7, 3, 10, 0, 3], [6, 0, 6, 2, 9, 12, 3], [6, 2, 6, 2, 9, 13, 3], [7, 1, 7, 0, 10, 0, 3], [7, 2, 6, 2, 9, 12, 3], [6, 2, 0, 2, 9, 12, 3], [6, 2, 6, 2, 10, 12, 3], [7, 1, 7, 1, 8, 0, 3], [7, 3, 7, 1, 10, 0, 3], [6, 2, 6, 0, 9, 12, 3], [6, 2, 6, 3, 9, 12, 3], [7, 1, 7, 1, 10, 0, 0]]
[v for v in a if a not in b]

[[7, 1, 7, 1, 10, 0, 3],
 [7, 1, 7, 1, 10, 0, 4],
 [7, 1, 7, 1, 10, 0, 1],
 [7, 1, 7, 1, 10, 0, 5],
 [7, 1, 7, 1, 10, 0, 2],
 [7, 1, 7, 1, 10, 0, 6],
 [7, 1, 7, 1, 10, 0, 0],
 [7, 0, 7, 1, 10, 0, 3],
 [7, 2, 7, 1, 10, 0, 3],
 [7, 3, 7, 1, 10, 0, 3],
 [4, 1, 7, 1, 10, 0, 3],
 [0, 1, 7, 1, 10, 0, 3],
 [1, 1, 7, 1, 10, 0, 3],
 [5, 1, 7, 1, 10, 0, 3],
 [2, 1, 7, 1, 10, 0, 3],
 [6, 1, 7, 1, 10, 0, 3],
 [3, 1, 7, 1, 10, 0, 3],
 [7, 1, 7, 0, 10, 0, 3],
 [7, 1, 7, 2, 10, 0, 3],
 [7, 1, 7, 3, 10, 0, 3],
 [7, 1, 4, 1, 10, 0, 3],
 [7, 1, 0, 1, 10, 0, 3],
 [7, 1, 1, 1, 10, 0, 3],
 [7, 1, 5, 1, 10, 0, 3],
 [7, 1, 2, 1, 10, 0, 3],
 [7, 1, 6, 1, 10, 0, 3],
 [7, 1, 3, 1, 10, 0, 3],
 [7, 1, 7, 1, 10, 10, 3],
 [7, 1, 7, 1, 10, 7, 3],
 [7, 1, 7, 1, 10, 4, 3],
 [7, 1, 7, 1, 10, 14, 3],
 [7, 1, 7, 1, 10, 1, 3],
 [7, 1, 7, 1, 10, 11, 3],
 [7, 1, 7, 1, 10, 8, 3],
 [7, 1, 7, 1, 10, 5, 3],
 [7, 1, 7, 1, 10, 2, 3],
 [7, 1, 7, 1, 10, 12, 3],
 [7, 1, 7, 1, 10, 9, 3],
 [7, 1, 7, 1, 10, 6, 3],
 [7, 1, 7, 1, 10, 3, 

In [199]:
runs = [[7, 1, 7, 1, 10, 0, 3], [7, 1, 7, 1, 10, 0, 4], [7, 1, 7, 1, 10, 0, 1], [7, 1, 7, 1, 10, 0, 5], [7, 1, 7, 1, 10, 0, 2], [7, 1, 7, 1, 10, 0, 6], [7, 1, 7, 1, 10, 0, 0], [7, 0, 7, 1, 10, 0, 3], [7, 2, 7, 1, 10, 0, 3], [7, 3, 7, 1, 10, 0, 3], [4, 1, 7, 1, 10, 0, 3], [0, 1, 7, 1, 10, 0, 3], [1, 1, 7, 1, 10, 0, 3], [5, 1, 7, 1, 10, 0, 3], [2, 1, 7, 1, 10, 0, 3], [6, 1, 7, 1, 10, 0, 3], [3, 1, 7, 1, 10, 0, 3], [7, 1, 7, 0, 10, 0, 3], [7, 1, 7, 2, 10, 0, 3], [7, 1, 7, 3, 10, 0, 3], [7, 1, 4, 1, 10, 0, 3], [7, 1, 0, 1, 10, 0, 3], [7, 1, 1, 1, 10, 0, 3], [7, 1, 5, 1, 10, 0, 3], [7, 1, 2, 1, 10, 0, 3], [7, 1, 6, 1, 10, 0, 3], [7, 1, 3, 1, 10, 0, 3], [7, 1, 7, 1, 10, 10, 3], [7, 1, 7, 1, 10, 7, 3], [7, 1, 7, 1, 10, 4, 3], [7, 1, 7, 1, 10, 14, 3], [7, 1, 7, 1, 10, 1, 3], [7, 1, 7, 1, 10, 11, 3], [7, 1, 7, 1, 10, 8, 3], [7, 1, 7, 1, 10, 5, 3], [7, 1, 7, 1, 10, 2, 3], [7, 1, 7, 1, 10, 12, 3], [7, 1, 7, 1, 10, 9, 3], [7, 1, 7, 1, 10, 6, 3], [7, 1, 7, 1, 10, 3, 3], [7, 1, 7, 1, 10, 13, 3], [7, 1, 7, 1, 7, 0, 3], [7, 1, 7, 1, 4, 0, 3], [7, 1, 7, 1, 0, 0, 3], [7, 1, 7, 1, 8, 0, 3], [7, 1, 7, 1, 1, 0, 3], [7, 1, 7, 1, 5, 0, 3], [7, 1, 7, 1, 2, 0, 3], [7, 1, 7, 1, 9, 0, 3], [7, 1, 7, 1, 6, 0, 3], [7, 1, 7, 1, 3, 0, 3]]

In [200]:
len(runs)

51

In [209]:
chris_files = f"""Perm_0_1_7_1_10_0_3_401.bzip2	Perm_6_2_6_2_2_12_3_401.bzip2	Perm_7_1_7_1_10_0_2_401.bzip2	Perm_7_1_7_1_1_0_3_401.bzip2
Perm_0_1_7_1_10_0_3_429.mcf	Perm_6_2_6_2_2_12_3_429.mcf	Perm_7_1_7_1_10_0_2_429.mcf	Perm_7_1_7_1_1_0_3_429.mcf
Perm_0_1_7_1_2_0_3_401.bzip2	Perm_6_2_6_3_1_12_3_401.bzip2	Perm_7_1_7_1_10_0_3_401.bzip2	Perm_7_1_7_1_2_0_0_401.bzip2
Perm_0_1_7_1_2_0_3_429.mcf	Perm_6_2_6_3_1_12_3_429.mcf	Perm_7_1_7_1_10_0_3_429.mcf	Perm_7_1_7_1_2_0_0_429.mcf
Perm_0_2_6_2_1_12_3_401.bzip2	Perm_6_2_7_2_1_12_3_401.bzip2	Perm_7_1_7_1_10_0_4_401.bzip2	Perm_7_1_7_1_2_0_3_401.bzip2
Perm_0_2_6_2_1_12_3_429.mcf	Perm_6_2_7_2_1_12_3_429.mcf	Perm_7_1_7_1_10_0_4_429.mcf	Perm_7_1_7_1_2_0_3_429.mcf
Perm_1_1_7_1_10_0_3_401.bzip2	Perm_6_3_6_2_1_12_3_401.bzip2	Perm_7_1_7_1_10_0_5_401.bzip2	Perm_7_1_7_1_2_0_6_401.bzip2
Perm_1_1_7_1_10_0_3_429.mcf	Perm_6_3_6_2_1_12_3_429.mcf	Perm_7_1_7_1_10_0_5_429.mcf	Perm_7_1_7_1_2_0_6_429.mcf
Perm_1_1_7_1_2_0_3_401.bzip2	Perm_7_0_7_1_10_0_3_401.bzip2	Perm_7_1_7_1_10_0_6_401.bzip2	Perm_7_1_7_1_2_14_3_401.bzip2
Perm_1_1_7_1_2_0_3_429.mcf	Perm_7_0_7_1_10_0_3_429.mcf	Perm_7_1_7_1_10_0_6_429.mcf	Perm_7_1_7_1_2_14_3_429.mcf
Perm_2_1_7_1_10_0_3_401.bzip2	Perm_7_0_7_1_2_0_3_401.bzip2	Perm_7_1_7_1_10_10_3_401.bzip2	Perm_7_1_7_1_3_0_3_401.bzip2
Perm_2_1_7_1_10_0_3_429.mcf	Perm_7_0_7_1_2_0_3_429.mcf	Perm_7_1_7_1_10_10_3_429.mcf	Perm_7_1_7_1_3_0_3_429.mcf
Perm_2_1_7_1_2_0_3_401.bzip2	Perm_7_1_0_1_10_0_3_401.bzip2	Perm_7_1_7_1_10_11_3_401.bzip2	Perm_7_1_7_1_4_0_3_401.bzip2
Perm_2_1_7_1_2_0_3_429.mcf	Perm_7_1_0_1_10_0_3_429.mcf	Perm_7_1_7_1_10_11_3_429.mcf	Perm_7_1_7_1_4_0_3_429.mcf
Perm_3_1_7_1_10_0_3_401.bzip2	Perm_7_1_0_1_2_0_3_401.bzip2	Perm_7_1_7_1_10_12_3_401.bzip2	Perm_7_1_7_1_5_0_3_401.bzip2
Perm_3_1_7_1_10_0_3_429.mcf	Perm_7_1_0_1_2_0_3_429.mcf	Perm_7_1_7_1_10_12_3_429.mcf	Perm_7_1_7_1_5_0_3_429.mcf
Perm_4_1_7_1_10_0_3_401.bzip2	Perm_7_1_1_1_10_0_3_401.bzip2	Perm_7_1_7_1_10_13_3_401.bzip2	Perm_7_1_7_1_6_0_3_401.bzip2
Perm_4_1_7_1_10_0_3_429.mcf	Perm_7_1_1_1_10_0_3_429.mcf	Perm_7_1_7_1_10_13_3_429.mcf	Perm_7_1_7_1_6_0_3_429.mcf
Perm_5_1_7_1_10_0_3_401.bzip2	Perm_7_1_2_1_10_0_3_401.bzip2	Perm_7_1_7_1_10_14_3_401.bzip2	Perm_7_1_7_1_7_0_3_401.bzip2
Perm_5_1_7_1_10_0_3_429.mcf	Perm_7_1_2_1_10_0_3_429.mcf	Perm_7_1_7_1_10_14_3_429.mcf	Perm_7_1_7_1_7_0_3_429.mcf
Perm_6_0_6_2_1_12_3_401.bzip2	Perm_7_1_3_1_10_0_3_401.bzip2	Perm_7_1_7_1_10_1_3_401.bzip2	Perm_7_1_7_1_8_0_3_401.bzip2
Perm_6_0_6_2_1_12_3_429.mcf	Perm_7_1_3_1_10_0_3_429.mcf	Perm_7_1_7_1_10_1_3_429.mcf	Perm_7_1_7_1_8_0_3_429.mcf
Perm_6_1_7_1_10_0_3_401.bzip2	Perm_7_1_4_1_10_0_3_401.bzip2	Perm_7_1_7_1_10_2_3_401.bzip2	Perm_7_1_7_1_9_0_3_401.bzip2
Perm_6_1_7_1_10_0_3_429.mcf	Perm_7_1_4_1_10_0_3_429.mcf	Perm_7_1_7_1_10_2_3_429.mcf	Perm_7_1_7_1_9_0_3_429.mcf
Perm_6_2_0_2_1_12_3_401.bzip2	Perm_7_1_5_1_10_0_3_401.bzip2	Perm_7_1_7_1_10_3_3_401.bzip2	Perm_7_1_7_2_10_0_3_401.bzip2
Perm_6_2_0_2_1_12_3_429.mcf	Perm_7_1_5_1_10_0_3_429.mcf	Perm_7_1_7_1_10_3_3_429.mcf	Perm_7_1_7_2_10_0_3_429.mcf
Perm_6_2_6_0_1_12_3_401.bzip2	Perm_7_1_6_1_10_0_3_401.bzip2	Perm_7_1_7_1_10_4_3_401.bzip2	Perm_7_1_7_3_10_0_3_401.bzip2
Perm_6_2_6_0_1_12_3_429.mcf	Perm_7_1_6_1_10_0_3_429.mcf	Perm_7_1_7_1_10_4_3_429.mcf	Perm_7_1_7_3_10_0_3_429.mcf
Perm_6_2_6_2_0_12_3_401.bzip2	Perm_7_1_7_0_10_0_3_401.bzip2	Perm_7_1_7_1_10_5_3_401.bzip2	Perm_7_1_7_3_2_0_3_401.bzip2
Perm_6_2_6_2_0_12_3_429.mcf	Perm_7_1_7_0_10_0_3_429.mcf	Perm_7_1_7_1_10_5_3_429.mcf	Perm_7_1_7_3_2_0_3_429.mcf
Perm_6_2_6_2_1_0_3_401.bzip2	Perm_7_1_7_0_2_0_3_401.bzip2	Perm_7_1_7_1_10_6_3_401.bzip2	Perm_7_2_6_2_1_12_3_401.bzip2
Perm_6_2_6_2_1_0_3_429.mcf	Perm_7_1_7_0_2_0_3_429.mcf	Perm_7_1_7_1_10_6_3_429.mcf	Perm_7_2_6_2_1_12_3_429.mcf
Perm_6_2_6_2_1_12_0_401.bzip2	Perm_7_1_7_1_0_0_3_401.bzip2	Perm_7_1_7_1_10_7_3_401.bzip2	Perm_7_2_7_1_10_0_3_401.bzip2
Perm_6_2_6_2_1_12_0_429.mcf	Perm_7_1_7_1_0_0_3_429.mcf	Perm_7_1_7_1_10_7_3_429.mcf	Perm_7_2_7_1_10_0_3_429.mcf
Perm_6_2_6_2_1_12_4_401.bzip2	Perm_7_1_7_1_10_0_0_401.bzip2	Perm_7_1_7_1_10_8_3_401.bzip2	Perm_7_3_7_1_10_0_3_401.bzip2
Perm_6_2_6_2_1_12_4_429.mcf	Perm_7_1_7_1_10_0_0_429.mcf	Perm_7_1_7_1_10_8_3_429.mcf	Perm_7_3_7_1_10_0_3_429.mcf
Perm_6_2_6_2_1_13_3_401.bzip2	Perm_7_1_7_1_10_0_1_401.bzip2	Perm_7_1_7_1_10_9_3_401.bzip2	Perm_7_3_7_1_2_0_3_401.bzip2
Perm_6_2_6_2_1_13_3_429.mcf	Perm_7_1_7_1_10_0_1_429.mcf	Perm_7_1_7_1_10_9_3_429.mcf	Perm_7_3_7_1_2_0_3_429.mcf""".split('\t')

In [213]:
chris_files = [j for i in [v.split('\n') for v in chris_files] for j in i]

In [214]:
chris_files

['Perm_0_1_7_1_10_0_3_401.bzip2',
 'Perm_6_2_6_2_2_12_3_401.bzip2',
 'Perm_7_1_7_1_10_0_2_401.bzip2',
 'Perm_7_1_7_1_1_0_3_401.bzip2',
 'Perm_0_1_7_1_10_0_3_429.mcf',
 'Perm_6_2_6_2_2_12_3_429.mcf',
 'Perm_7_1_7_1_10_0_2_429.mcf',
 'Perm_7_1_7_1_1_0_3_429.mcf',
 'Perm_0_1_7_1_2_0_3_401.bzip2',
 'Perm_6_2_6_3_1_12_3_401.bzip2',
 'Perm_7_1_7_1_10_0_3_401.bzip2',
 'Perm_7_1_7_1_2_0_0_401.bzip2',
 'Perm_0_1_7_1_2_0_3_429.mcf',
 'Perm_6_2_6_3_1_12_3_429.mcf',
 'Perm_7_1_7_1_10_0_3_429.mcf',
 'Perm_7_1_7_1_2_0_0_429.mcf',
 'Perm_0_2_6_2_1_12_3_401.bzip2',
 'Perm_6_2_7_2_1_12_3_401.bzip2',
 'Perm_7_1_7_1_10_0_4_401.bzip2',
 'Perm_7_1_7_1_2_0_3_401.bzip2',
 'Perm_0_2_6_2_1_12_3_429.mcf',
 'Perm_6_2_7_2_1_12_3_429.mcf',
 'Perm_7_1_7_1_10_0_4_429.mcf',
 'Perm_7_1_7_1_2_0_3_429.mcf',
 'Perm_1_1_7_1_10_0_3_401.bzip2',
 'Perm_6_3_6_2_1_12_3_401.bzip2',
 'Perm_7_1_7_1_10_0_5_401.bzip2',
 'Perm_7_1_7_1_2_0_6_401.bzip2',
 'Perm_1_1_7_1_10_0_3_429.mcf',
 'Perm_6_3_6_2_1_12_3_429.mcf',
 'Perm_7_1_7_1_10

In [215]:
'\n'.join(chris_files)

'Perm_0_1_7_1_10_0_3_401.bzip2\nPerm_6_2_6_2_2_12_3_401.bzip2\nPerm_7_1_7_1_10_0_2_401.bzip2\nPerm_7_1_7_1_1_0_3_401.bzip2\nPerm_0_1_7_1_10_0_3_429.mcf\nPerm_6_2_6_2_2_12_3_429.mcf\nPerm_7_1_7_1_10_0_2_429.mcf\nPerm_7_1_7_1_1_0_3_429.mcf\nPerm_0_1_7_1_2_0_3_401.bzip2\nPerm_6_2_6_3_1_12_3_401.bzip2\nPerm_7_1_7_1_10_0_3_401.bzip2\nPerm_7_1_7_1_2_0_0_401.bzip2\nPerm_0_1_7_1_2_0_3_429.mcf\nPerm_6_2_6_3_1_12_3_429.mcf\nPerm_7_1_7_1_10_0_3_429.mcf\nPerm_7_1_7_1_2_0_0_429.mcf\nPerm_0_2_6_2_1_12_3_401.bzip2\nPerm_6_2_7_2_1_12_3_401.bzip2\nPerm_7_1_7_1_10_0_4_401.bzip2\nPerm_7_1_7_1_2_0_3_401.bzip2\nPerm_0_2_6_2_1_12_3_429.mcf\nPerm_6_2_7_2_1_12_3_429.mcf\nPerm_7_1_7_1_10_0_4_429.mcf\nPerm_7_1_7_1_2_0_3_429.mcf\nPerm_1_1_7_1_10_0_3_401.bzip2\nPerm_6_3_6_2_1_12_3_401.bzip2\nPerm_7_1_7_1_10_0_5_401.bzip2\nPerm_7_1_7_1_2_0_6_401.bzip2\nPerm_1_1_7_1_10_0_3_429.mcf\nPerm_6_3_6_2_1_12_3_429.mcf\nPerm_7_1_7_1_10_0_5_429.mcf\nPerm_7_1_7_1_2_0_6_429.mcf\nPerm_1_1_7_1_2_0_3_401.bzip2\nPerm_7_0_7_1_10_0_3